In [6]:
from data import getdata
from dotenv import load_dotenv
from typing import Optional
import os
import yaml
import pandas as pd
import vectorbt as vbt
import numpy as np

load_dotenv()
config_path = os.getenv('3CANDLES_CONFIG_PATH')

with open(config_path, 'r') as file:
        config = yaml.safe_load(file)
    
df_hour = pd.read_csv(config['Data_filename'])
df_hour = df_hour.set_index('Time')
df_hour.index = pd.to_datetime(df_hour.index)

df_hour = df_hour.drop(columns=['Volume', 'High', 'Low'])
df_hour['Dir'] = 0

df_hour.loc[df_hour['Close'] > df_hour['Open'], 'Dir'] = 1
bull_entry_mask = ((df_hour['Dir'] == 1) & (df_hour['Dir'].shift(1) == 1) & (df_hour['Dir'].shift(2) == 1) & #short
                    (df_hour['Close'].shift(2) < df_hour['Open']))
df_hour['Bull Entry'] = bull_entry_mask
bear_entry_mask = ((df_hour['Dir'] == 0) & (df_hour['Dir'].shift(1) == 0) & (df_hour['Dir'].shift(2) == 0) & #long
                    (df_hour['Close'].shift(2) > df_hour['Open']))
df_hour['Bear Entry'] = bear_entry_mask

df_hour.loc[df_hour['Bull Entry'] == True, 'SL'] = df_hour['Close'] #short
df_hour.loc[df_hour['Bear Entry'] == True, 'SL'] = df_hour['Close'] #long

df_hour.loc[df_hour['Bull Entry'] == True, 'TP'] = df_hour['Close'] - (df_hour['Close'] - df_hour['Close'].shift(2)) #short
df_hour.loc[df_hour['Bear Entry'] == True, 'TP'] = df_hour['Close'] + ((df_hour['Close'] - df_hour['Close'].shift(2)) * -1) #long

index_arr_hour = df_hour.index.to_numpy()
open_arr_hour = df_hour['Open'].to_numpy()
close_arr_hour = df_hour['Close'].to_numpy()
bull_entry_arr_hour = df_hour['Bull Entry'].to_numpy()
bear_entry_arr_hour = df_hour['Bear Entry'].to_numpy()
sl_arr_hour = df_hour['SL'].to_numpy()
tp_arr_hour = df_hour['TP'].to_numpy()
price_arr_hour = np.full(len(index_arr_hour), np.nan)
bull_entrymask_arr_hour = np.full(len(index_arr_hour), False)
bear_entrymask_arr_hour = np.full(len(index_arr_hour), False)
bull_exit_arr_hour = np.full(len(index_arr_hour), False)
bear_exit_arr_hour = np.full(len(index_arr_hour), False)

trade_direct: Optional[str] = None
cur_sl: Optional[float] = None; cur_tp: Optional[float] = None

for i in range(len(index_arr_hour)):
    if trade_direct is None:

        if bull_entry_arr_hour[i]:
            trade_direct = 'bull'
            bull_entrymask_arr_hour[i] = True
            cur_sl, cur_tp = sl_arr_hour[i], tp_arr_hour[i]
            price_arr_hour[i] = close_arr_hour[i]
        elif bear_entry_arr_hour[i]:
            trade_direct = 'bear'
            bear_entrymask_arr_hour[i] = True
            cur_sl, cur_tp = sl_arr_hour[i], tp_arr_hour[i]
            price_arr_hour[i] = close_arr_hour[i]
        else:
            continue  

    elif trade_direct == 'bull':

        if close_arr_hour[i] >= cur_sl:
            price_arr_hour[i] = cur_sl
            trade_direct, cur_sl, cur_tp = None, None, None
            bull_exit_arr_hour[i] = True
        elif close_arr_hour[i] <= cur_tp:
            price_arr_hour[i] = cur_tp
            trade_direct, cur_sl, cur_tp = None, None, None
            bull_exit_arr_hour[i] = True

    elif trade_direct == 'bear':

        if close_arr_hour[i] <= cur_sl:
            price_arr_hour[i] = cur_sl
            trade_direct, cur_sl, cur_tp = None, None, None
            bear_exit_arr_hour[i] = True
        elif close_arr_hour[i] >= cur_tp:
            price_arr_hour[i] = cur_tp
            trade_direct, cur_sl, cur_tp = None, None, None
            bear_exit_arr_hour[i] = True

pf = vbt.Portfolio.from_signals(
entries = bear_entrymask_arr_hour,
exits = bear_exit_arr_hour,
short_entries = bull_entrymask_arr_hour,
short_exits = bull_exit_arr_hour,
price = price_arr_hour,
open = df_hour["Open"],
close = df_hour["Close"],
size = config['Trade']['size'],
size_type = config['Trade']['size_type'],
fees = config['Broker']['fees'],
fixed_fees = config['Broker']['fixed_fees'],
slippage = config['Slippage'],
init_cash = config['Initial_cash'],
freq = config['Frequency']
)

In [7]:
pf.stats()

Start                         2024-01-01 22:00:00+00:00
End                           2025-12-02 21:00:00+00:00
Period                                499 days 00:00:00
Start Value                                     55000.0
End Value                                   55000.50927
Total Return [%]                               0.000926
Benchmark Return [%]                           5.229516
Max Gross Exposure [%]                         0.002156
Total Fees Paid                                     0.0
Max Drawdown [%]                               0.000015
Max Drawdown Duration                   5 days 22:00:00
Total Trades                                       1612
Total Closed Trades                                1611
Total Open Trades                                     1
Open Trade PnL                                   0.0002
Win Rate [%]                                  28.988206
Best Trade [%]                                 1.228647
Worst Trade [%]                                 

In [9]:
pf.plot().show()

In [ ]:
pf.trades.records_readable()